In [1]:
gameweek = 1

In [2]:
import numpy as np
import pandas as pd
import json
import requests

import matplotlib.pyplot as plt
import plotly.graph_objects as go

# allow more data columns/rows to be shown than by default
pd.set_option('display.max_columns', 501)
pd.set_option('display.max_rows', 501)

# Data

In [3]:
player_data = pd.read_csv('../data/data_for_projections.csv', index_col=0)
player_data = player_data[player_data['season']=='2022-23'].copy()
player_data = player_data.rename(columns={'GW':'gameweek', 'opp_team_name':'opp_team'})
player_data

penalties_missed  influence   season  saves  transfers_in  \
42058                 0       22.0  2022-23      0         35508   
41917                 0       10.0  2022-23      0          3276   
41915                 0        0.4  2022-23      0          3527   
42048                 0       22.4  2022-23      0          2360   
41868                 0        7.8  2022-23      0           925   
42009                 0       28.6  2022-23      0         37390   
41886                 0       19.0  2022-23      0         35699   
41946                 0       10.8  2022-23      0          2287   
41871                 0       24.8  2022-23      0         41966   
42065                 0       19.8  2022-23      0         38444   
41920                 0        5.6  2022-23      0          9486   
41989                 0       14.4  2022-23      1        116936   
42046                 0       43.6  2022-23      0         46323   
41825                 0        7.4  2022-23      0         91328   
41813                 0       16.6  2022-23      0          8050   
42043                 0       14.6  2022-23      0         24720   
41999                 0       18.0  2022-23      0          4598   
42044                 0       36.2  2022-23      0         34255   
42042                 0       10.8  2022-23      1          9395   
42030                 0       12.2  2022-23      0           100   
41969                 0        3.2  2022-23      0         10030   
41926                 0       30.4  2022-23      0          7096   
42032                 0       49.2  2022-23      0        146412   
41945                 0       26.4  2022-23      0         14912   
41971                 0       30.4  2022-23      0         10077   
41903                 0       16.4  2022-23      0          3400   
41970                 0        8.2  2022-23      0          9950   
41916                 0       35.0  2022-23      5         34577   
41985                 0       24.4  2022-23      0        106587   
42061                 0       13.0  2022-23      0         12887   
41983                 0        6.6  2022-23      0        153135   
42034                 0       20.2  2022-23      0          4349   
41873                 0       12.2  2022-23      0         23244   
42057                 0        1.2  2022-23      0          5272   
41902                 0        0.8  2022-23      0          5440   
42002                 0        1.8  2022-23      0         36116   
41976                 0       39.6  2022-23      0        157420   
41888                 0       27.4  2022-23      0         46633   
41990                 0       26.2  2022-23      0         42388   
42029                 0        0.0  2022-23      0           166   
42028                 0        6.2  2022-23      0           231   
41872                 0       72.0  2022-23      0        239218   
41898                 0        7.0  2022-23      0         17941   
41986                 0        2.0  2022-23      0         20188   
41973                 0        7.4  2022-23      0          5329   
41889                 0        5.6  2022-23      0           334   
42016                 0        2.2  2022-23      0           609   
41929                 0        0.0  2022-23      0           944   
41978                 0       12.2  2022-23      0         51811   
41950                 0        9.8  2022-23      0          3276   
41904                 0       13.6  2022-23      0         20622   
41890                 0        3.2  2022-23      0         54673   
42013                 0       34.2  2022-23      0         38614   
41984                 0        3.8  2022-23      0         17252   
42017                 0        0.0  2022-23      0         17171   
41905                 0       13.4  2022-23      0           741   
41943                 0       14.0  2022-23      0          1820   
42060                 0        0.0  2022-23      0          416

In [4]:
latest_fpl = pd.read_csv(f'../data/fpl_data/fpl_week_{gameweek}.csv', index_col=0)
latest_fpl

chance_of_playing_next_round  chance_of_playing_this_round    code  \
id                                                                        
1                             NaN                           NaN   58822   
3                             NaN                           NaN   84450   
4                             NaN                           NaN  153256   
5                             NaN                           NaN  156074   
6                             NaN                           NaN  167199   
..                            ...                           ...     ...   
558                           NaN                           NaN  490721   
566                           NaN                           NaN  240299   
567                           NaN                           NaN  198842   
568                           NaN                           NaN  461026   
579                           NaN                           NaN  181284   

     cost_change_event  cost_change_event_fall  cost_change_start  \
id                                                                  
1                    0                       0                  0   
3                    0                       0                  0   
4                    0                       0                  0   
5                    0                       0                  0   
6                    0                       0                  0   
..                 ...                     ...                ...   
558                  0                       0                  0   
566                  0                       0                  0   
567                  0                       0                  0   
568                  0                       0                  0   
579                  0                       0                  0   

     cost_change_start_fall  dreamteam_count  element_type  ep_next  ep_this  \
id                                                                             
1                         0                0             2      2.4      2.4   
3                         0                0             3      2.1      2.1   
4                         0                0             3      1.5      1.5   
5                         0                0             2      2.4      2.4   
6                         0                0             3      2.1      2.1   
..                      ...              ...           ...      ...      ...   
558                       0                0             2      1.5      1.5   
566                       0                0             3      1.5      1.5   
567                       0                0             3      1.5      1.5   
568                       0                0             3      1.5      1.5   
579                       0                0             3      2.7      2.7   

     event_points      first_name  form  in_dreamteam news news_added  \
id                                                                      
1               0          Cédric   0.0         False  NaN        NaN   
3               2          Granit   2.0         False  NaN        NaN   
4               0         Mohamed   0.0         False  NaN        NaN   
5               0             Rob   0.0         False  NaN        NaN   
6               3          Thomas   3.0         False  NaN        NaN   
..            ...             ...   ...           ...  ...        ...   
558             0            Hugo   0.0         False  NaN        NaN   
566             0          Joseph   0.0         False  NaN        NaN   
567             0          Connor   0.0         False  NaN        NaN   
568             1            Chem   1.0         False  NaN        NaN   
579             0  Gonçalo Manuel   0.0         False  NaN        NaN   

     now_cost       photo  points_per_game       second_name  \
id                                                             
1          4

In [36]:
projections = pd.read_csv(f'../data/xP_projections_week{gameweek}.csv', index_col=0)
projections = projections.rename(columns={'xP':'projected_points'})
projections

name       team         opp_team  was_home  gameweek  \
0     Granit Xhaka    Arsenal   Leicester City         1         2   
1     Granit Xhaka    Arsenal      Bournemouth         0         3   
2     Granit Xhaka    Arsenal           Fulham         1         4   
3     Granit Xhaka    Arsenal      Aston Villa         1         5   
4     Granit Xhaka    Arsenal   Manchester Utd         0         6   
...            ...        ...              ...       ...       ...   
4425  Darwin Nunez  Liverpool           Wolves         1         7   
4426  Darwin Nunez  Liverpool          Chelsea         0         8   
4427  Darwin Nunez  Liverpool         Brighton         1         9   
4428  Darwin Nunez  Liverpool          Arsenal         0        10   
4429  Darwin Nunez  Liverpool  Manchester City         1        11   

      projected_points  
0             2.558866  
1             2.623845  
2             2.599292  
3             2.621276  
4             2.440373  
...                ...  
4425          6.084837  
4426          2.923533  
4427          3.922148  
4428          4.514771  
4429          4.614263  

[4430 rows x 6 columns]

In [37]:
projections['position'] = [latest_fpl.loc[latest_fpl['name']==name, 'element_type'].values[0] for name in projections['name']]
position_dict={1:'GK', 2:'DEF', 3:'MID', 4:'FWD'}
projections['position'] = projections['position'].map(position_dict)
projections['position'] = pd.Categorical(projections['position'], ['GK','DEF','MID','FWD'])
projections

name       team         opp_team  was_home  gameweek  \
0     Granit Xhaka    Arsenal   Leicester City         1         2   
1     Granit Xhaka    Arsenal      Bournemouth         0         3   
2     Granit Xhaka    Arsenal           Fulham         1         4   
3     Granit Xhaka    Arsenal      Aston Villa         1         5   
4     Granit Xhaka    Arsenal   Manchester Utd         0         6   
...            ...        ...              ...       ...       ...   
4425  Darwin Nunez  Liverpool           Wolves         1         7   
4426  Darwin Nunez  Liverpool          Chelsea         0         8   
4427  Darwin Nunez  Liverpool         Brighton         1         9   
4428  Darwin Nunez  Liverpool          Arsenal         0        10   
4429  Darwin Nunez  Liverpool  Manchester City         1        11   

      projected_points position  
0             2.558866      MID  
1             2.623845      MID  
2             2.599292      MID  
3             2.621276      MID  
4             2.440373      MID  
...                ...      ...  
4425          6.084837      FWD  
4426          2.923533      FWD  
4427          3.922148      FWD  
4428          4.514771      FWD  
4429          4.614263      FWD  

[4430 rows x 7 columns]

In [38]:
preseason_projections = pd.read_csv('../data/pre_season_projections.csv', index_col=0)
preseason_projections = preseason_projections.rename(columns={'xP':'projected_points'})
preseason_projections

name       team         opp_team  was_home  gameweek  \
0   Cedric Alves Soares    Arsenal   Crystal Palace         0         1   
1   Cedric Alves Soares    Arsenal   Leicester City         1         2   
2   Cedric Alves Soares    Arsenal      Bournemouth         0         3   
3   Cedric Alves Soares    Arsenal           Fulham         1         4   
4   Cedric Alves Soares    Arsenal      Aston Villa         1         5   
..                  ...        ...              ...       ...       ...   
5          Ivan Perisic  Tottenham           Fulham         1         6   
6          Ivan Perisic  Tottenham  Manchester City         0         7   
7          Ivan Perisic  Tottenham   Leicester City         1         8   
8          Ivan Perisic  Tottenham          Arsenal         0         9   
9          Ivan Perisic  Tottenham         Brighton         0        10   

    projected_points  
0           2.535732  
1           2.939537  
2           2.762569  
3           3.002753  
4           2.849209  
..               ...  
5           5.022785  
6           3.032787  
7           4.320365  
8           3.500115  
9           3.468761  

[3790 rows x 6 columns]

In [39]:
# add previous points and xPoints to projections
for player_name in projections['name'].unique():
    indiv_data = player_data.loc[player_data['name']==player_name,['name','team','opp_team','was_home','gameweek',
                                                      'xPoints', 'total_points']]
    indiv_preseason_xp = preseason_projections.loc[(preseason_projections['name']==player_name) & \
                                                 (preseason_projections['gameweek']==1), 'projected_points']
    if indiv_preseason_xp.shape[0]==1:
        indiv_data['projected_points'] = indiv_preseason_xp.values[0]
    projections = pd.concat([projections, indiv_data])

display(projections)

name             team        opp_team  was_home  gameweek  \
0        Granit Xhaka          Arsenal  Leicester City         1         2   
1        Granit Xhaka          Arsenal     Bournemouth         0         3   
2        Granit Xhaka          Arsenal          Fulham         1         4   
3        Granit Xhaka          Arsenal     Aston Villa         1         5   
4        Granit Xhaka          Arsenal  Manchester Utd         0         6   
...               ...              ...             ...       ...       ...   
42082  Nathan Collins           Wolves    Leeds United         0         1   
42083   Chem Campbell           Wolves    Leeds United         0         1   
41995  Erling Haaland  Manchester City        West Ham         0         1   
42055    Ivan Perisic        Tottenham     Southampton         1         1   
41982    Darwin Nunez        Liverpool          Fulham         0         1   

       projected_points position    xPoints  total_points  
0              2.558866      MID        NaN           NaN  
1              2.623845      MID        NaN           NaN  
2              2.599292      MID        NaN           NaN  
3              2.621276      MID        NaN           NaN  
4              2.440373      MID        NaN           NaN  
...                 ...      ...        ...           ...  
42082          3.010083      NaN   4.083261           1.0  
42083               NaN      NaN   1.000089           1.0  
41995               NaN      NaN  11.123593          13.0  
42055          5.191961      NaN   0.976312           1.0  
41982               NaN      NaN   8.327932           9.0  

[4701 rows x 9 columns]

In [40]:
projections[projections['name']=='Harry Kane'].sort_values(by='gameweek')

name       team           opp_team  was_home  gameweek  \
42043  Harry Kane  Tottenham        Southampton         1         1   
3790   Harry Kane  Tottenham            Chelsea         0         2   
3791   Harry Kane  Tottenham             Wolves         1         3   
3792   Harry Kane  Tottenham  Nottingham Forest         0         4   
3793   Harry Kane  Tottenham           West Ham         0         5   
3794   Harry Kane  Tottenham             Fulham         1         6   
3795   Harry Kane  Tottenham    Manchester City         0         7   
3796   Harry Kane  Tottenham     Leicester City         1         8   
3797   Harry Kane  Tottenham            Arsenal         0         9   
3798   Harry Kane  Tottenham           Brighton         0        10   
3799   Harry Kane  Tottenham            Everton         1        11   

       projected_points position  xPoints  total_points  
42043          5.944536      NaN  3.00018           2.0  
3790           4.532984      FWD      NaN           NaN  
3791           7.325706      FWD      NaN           NaN  
3792           7.674112      FWD      NaN           NaN  
3793           5.577790      FWD      NaN           NaN  
3794           5.442252      FWD      NaN           NaN  
3795           3.742036      FWD      NaN           NaN  
3796           4.306097      FWD      NaN           NaN  
3797           4.638828      FWD      NaN           NaN  
3798           4.753438      FWD      NaN           NaN  
3799           6.802753      FWD      NaN           NaN

In [80]:
# player statistics
# maybe add points per appearance
player_stats = player_data.groupby('name').mean()[['xPoints']]
player_stats['points_per_game'] = [player_data.loc[player_data['name']==name, 'total_points'].sum() / \
                 player_data.loc[player_data['name']==name, 'total_points'].shape[0] for name in player_stats.index]
player_stats['price'] = [latest_fpl.loc[latest_fpl['name']==name, 'value'].values[0] for name in player_stats.index]
player_stats['team'] = [latest_fpl.loc[latest_fpl['name']==name, 'team'].values[0] for name in player_stats.index]
player_stats['value'] = player_stats['xPoints'] / player_stats['price']
player_stats['value_points'] = np.sqrt(player_stats['xPoints'] * player_stats['value'])
#position info
player_stats['position'] = [latest_fpl.loc[latest_fpl['name']==name, 'element_type'].values[0] \
                                                                        for name in player_stats.index]
position_dict={1:'GK', 2:'DEF', 3:'MID', 4:'FWD'}
player_stats['position'] = player_stats['position'].map(position_dict)
player_stats['position'] = pd.Categorical(player_stats['position'], ['GK','DEF','MID','FWD'])

player_stats['minutes_played'] = [player_data.loc[player_data['name']==name, 'General_Min'].sum() \
                                                                          for name in player_stats.index]
# reorder columns
player_stats = player_stats[['team','position','price','minutes_played','xPoints', 'points_per_game', 'value','value_points']]
player_stats

team position  price  minutes_played  \
name                                                                      
Aaron Cresswell                West Ham      DEF    5.0            90.0   
Aaron Hickey                  Brentford      DEF    5.0            82.0   
Aaron Ramsdale                  Arsenal       GK    5.0            90.0   
Abdoulaye Doucoure              Everton      MID    5.5            90.0   
Adam Armstrong              Southampton      FWD    5.5            45.0   
Adam Lallana                   Brighton      MID    5.0            75.0   
Adam Smith                  Bournemouth      DEF    4.5            90.0   
Adam Webster                   Brighton      DEF    4.5            90.0   
Albert Sambi Lokonga            Arsenal      MID    4.5             1.0   
Alejandro Garnacho       Manchester Utd      MID    4.5             1.0   
Aleksandar Mitrovic              Fulham      FWD    6.6            90.0   
Alex Iwobi                      Everton      MID    5.5            90.0   
Alexis Mac Allister            Brighton      MID    5.5            90.0   
Alisson                       Liverpool       GK    5.5            90.0   
Allan Saint-Maximin       Newcastle Utd      MID    6.5            89.0   
Alphonse Areola                West Ham       GK    4.5            62.0   
Andreas Pereira                  Fulham      MID    4.5            88.0   
Andrew Robertson              Liverpool      DEF    7.0            90.0   
Anthony Elanga           Manchester Utd      MID    5.0             1.0   
Anthony Gordon                  Everton      MID    5.5            90.0   
Antonee Robinson                 Fulham      DEF    4.5            90.0   
Armando Broja                   Chelsea      FWD    5.5            16.0   
Ben Chilwell                    Chelsea      DEF    6.0            64.0   
Ben Davies                    Liverpool      DEF    4.0            85.0   
Ben Godfrey                     Everton      DEF    4.5            17.0   
Ben Johnson                    West Ham      DEF    4.5            90.0   
Ben Mee                       Brentford      DEF    4.5            58.0   
Ben Pearson                 Bournemouth      MID    4.5            71.0   
Ben White                       Arsenal      DEF    4.5            90.0   
Bobby De Cordova-Reid            Fulham      MID    5.5            89.0   
Boubacar Kamara             Aston Villa      MID    5.0            81.0   
Brenden Aaronson           Leeds United      MID    5.5            83.0   
Bruno Fernandes          Manchester Utd      MID   10.0            89.0   
Bruno Guimaraes           Newcastle Utd      MID    6.0            89.0   
Bryan Mbeumo                  Brentford      FWD    6.0            90.0   
Bukayo Saka                     Arsenal      MID    8.0            90.0   
Callum Wilson             Newcastle Utd      FWD    7.5            89.0   
Cameron Archer              Aston Villa      FWD    4.5            10.0   
Cesar Azpilicueta               Chelsea      DEF    5.0            90.0   
Cheick Doucoure          Crystal Palace      MID    5.0            74.0   
Chem Campbell                    Wolves      MID    4.5             6.0   
Chris Mepham                Bournemouth      DEF    4.5            90.0   
Chris Wood                Newcastle Utd      FWD    6.0             1.0   
Christian Eriksen        Manchester Utd      MID    6.5            90.0   
Christian Nrgaard             Brentford      MID    5.5            72.0   
Christian Pulisic               Chelsea      MID    6.0            26.0   
Clement Lenglet               Tottenham      DEF    5.0             5.0   
Cole Palmer             Manchester City      MID    4.5             3.0   
Conor Coventry                 West Ham      MID    4.5             1.0   
Conor Gallagher                 Chelsea      MID    5.9             1.0   
Cristian Romero               Tottenham      DEF    5.0            90.0   
Cristiano Ronaldo        Manchester Utd      FWD   10.5     

In [77]:
[player_data.loc[player_data['name']==name, 'total_points'].sum() / \
 player_data.loc[player_data['name']==name, 'total_points'].shape[0] for name in player_stats.index]

[1.0,
 1.0,
 6.0,
 2.0,
 1.0,
 2.0,
 5.0,
 2.0,
 1.0,
 1.0,
 13.0,
 2.0,
 0.0,
 1.0,
 3.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 1.0,
 1.0,
 9.0,
 2.0,
 1.0,
 1.0,
 0.0,
 2.0,
 5.0,
 1.0,
 2.0,
 2.0,
 2.0,
 3.0,
 2.0,
 6.0,
 6.0,
 1.0,
 7.0,
 2.0,
 1.0,
 7.0,
 1.0,
 2.0,
 2.0,
 1.0,
 1.0,
 1.0,
 1.0,
 1.0,
 2.0,
 1.0,
 1.0,
 6.0,
 1.0,
 10.0,
 1.0,
 1.0,
 7.0,
 9.0,
 2.0,
 2.0,
 13.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 7.0,
 7.0,
 1.0,
 1.0,
 1.0,
 8.0,
 13.0,
 1.0,
 15.0,
 1.0,
 1.0,
 7.0,
 2.0,
 1.0,
 1.0,
 2.0,
 4.0,
 2.0,
 2.0,
 0.0,
 1.0,
 5.0,
 2.0,
 5.0,
 1.0,
 3.0,
 3.0,
 1.0,
 8.0,
 3.0,
 6.0,
 0.0,
 1.0,
 0.0,
 2.0,
 1.0,
 5.0,
 1.0,
 2.0,
 9.0,
 5.0,
 0.0,
 2.0,
 1.0,
 10.0,
 2.0,
 1.0,
 7.0,
 2.0,
 1.0,
 3.0,
 1.0,
 2.0,
 6.0,
 2.0,
 1.0,
 2.0,
 2.0,
 3.0,
 6.0,
 2.0,
 6.0,
 1.0,
 1.0,
 2.0,
 6.0,
 1.0,
 1.0,
 3.0,
 6.0,
 6.0,
 1.0,
 7.0,
 10.0,
 1.0,
 6.0,
 0.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 0.0,
 12.0,
 1.0,
 1.0,
 2.0,
 1.0,
 1.0,
 0.0,
 1.0,
 1

# Analysis

In [12]:
# top players for each gameweek
for week in range(gameweek+1,gameweek+11):
    print(f'Gameweek {week}:')
    display(projections.loc[projections['gameweek']==week].sort_values(by='projected_points', ascending=False).head(15))
    print()

Gameweek 2:


name             team        opp_team  was_home  \
2640           Mohamed Salah        Liverpool  Crystal Palace         1   
3030         Bruno Fernandes   Manchester Utd       Brentford         0   
2810         Kevin De Bruyne  Manchester City     Bournemouth         1   
4400          Erling Haaland  Manchester City     Bournemouth         1   
2830            Riyad Mahrez  Manchester City     Bournemouth         1   
2850            Joao Cancelo  Manchester City     Bournemouth         1   
2980       Cristiano Ronaldo   Manchester Utd       Brentford         0   
190            Gabriel Jesus          Arsenal  Leicester City         1   
2910              Phil Foden  Manchester City     Bournemouth         1   
90               Bukayo Saka          Arsenal  Leicester City         1   
2660  Trent Alexander-Arnold        Liverpool  Crystal Palace         1   
2730               Luis Diaz        Liverpool  Crystal Palace         1   
4420            Darwin Nunez        Liverpool  Crystal Palace         1   
2840           Jack Grealish  Manchester City     Bournemouth         1   
320            Ollie Watkins      Aston Villa         Everton         1   

      gameweek  projected_points position  xPoints  total_points  
2640         2          6.752071      MID      NaN           NaN  
3030         2          6.574602      MID      NaN           NaN  
2810         2          5.857881      MID      NaN           NaN  
4400         2          5.696524      FWD      NaN           NaN  
2830         2          5.590813      MID      NaN           NaN  
2850         2          5.284076      DEF      NaN           NaN  
2980         2          5.153364      FWD      NaN           NaN  
190          2          4.913856      FWD      NaN           NaN  
2910         2          4.913840      MID      NaN           NaN  
90           2          4.880308      MID      NaN           NaN  
2660         2          4.823452      DEF      NaN           NaN  
2730         2          4.732542      MID      NaN           NaN  
4420         2          4.617370      FWD      NaN           NaN  
2840         2          4.569909      MID      NaN           NaN  
320          2          4.565567      FWD      NaN           NaN


Gameweek 3:


name             team        opp_team  was_home  gameweek  \
3791        Harry Kane        Tottenham          Wolves         1         3   
1431       Will Hughes   Crystal Palace     Aston Villa         1         3   
2641     Mohamed Salah        Liverpool  Manchester Utd         0         3   
1301   Raheem Sterling          Chelsea    Leeds United         0         3   
4401    Erling Haaland  Manchester City   Newcastle Utd         0         3   
3801     Heung-Min Son        Tottenham          Wolves         1         3   
2811   Kevin De Bruyne  Manchester City   Newcastle Utd         0         3   
91         Bukayo Saka          Arsenal     Bournemouth         0         3   
4421      Darwin Nunez        Liverpool  Manchester Utd         0         3   
1201       Mason Mount          Chelsea    Leeds United         0         3   
4411      Ivan Perisic        Tottenham          Wolves         1         3   
2831      Riyad Mahrez  Manchester City   Newcastle Utd         0         3   
3961  Dejan Kulusevski        Tottenham          Wolves         1         3   
2911        Phil Foden  Manchester City   Newcastle Utd         0         3   
191      Gabriel Jesus          Arsenal     Bournemouth         0         3   

      projected_points position  xPoints  total_points  
3791          7.325706      FWD      NaN           NaN  
1431          6.281170      MID      NaN           NaN  
2641          6.263748      MID      NaN           NaN  
1301          6.125771      MID      NaN           NaN  
4401          6.080535      FWD      NaN           NaN  
3801          6.000802      MID      NaN           NaN  
2811          5.702351      MID      NaN           NaN  
91            5.500435      MID      NaN           NaN  
4421          5.277286      FWD      NaN           NaN  
1201          5.067535      MID      NaN           NaN  
4411          5.035127      DEF      NaN           NaN  
2831          4.775721      MID      NaN           NaN  
3961          4.775281      MID      NaN           NaN  
2911          4.714697      MID      NaN           NaN  
191           4.703760      FWD      NaN           NaN


Gameweek 4:


...

name             team           opp_team  was_home  \
2647     Mohamed Salah        Liverpool           Brighton         1   
2817   Kevin De Bruyne  Manchester City     Manchester Utd         1   
4107      Jarrod Bowen         West Ham             Wolves         1   
2837      Riyad Mahrez  Manchester City     Manchester Utd         1   
4407    Erling Haaland  Manchester City     Manchester Utd         1   
3967  Dejan Kulusevski        Tottenham            Arsenal         0   
2857      Joao Cancelo  Manchester City     Manchester Utd         1   
1307   Raheem Sterling          Chelsea     Crystal Palace         0   
637         Ivan Toney        Brentford        Bournemouth         0   
2917        Phil Foden  Manchester City     Manchester Utd         1   
2117       Jamie Vardy   Leicester City  Nottingham Forest         1   
3797        Harry Kane        Tottenham            Arsenal         0   
2197     Harvey Barnes   Leicester City  Nottingham Forest         1   
1207       Mason Mount          Chelsea     Crystal Palace         0   
3807     Heung-Min Son        Tottenham            Arsenal         0   

      gameweek  projected_points position  xPoints  total_points  
2647         9          7.053408      MID      NaN           NaN  
2817         9          6.527099      MID      NaN           NaN  
4107         9          5.629486      MID      NaN           NaN  
2837         9          5.562489      MID      NaN           NaN  
4407         9          5.344519      FWD      NaN           NaN  
3967         9          4.982694      MID      NaN           NaN  
2857         9          4.952462      DEF      NaN           NaN  
1307         9          4.917990      MID      NaN           NaN  
637          9          4.687969      FWD      NaN           NaN  
2917         9          4.646339      MID      NaN           NaN  
2117         9          4.642954      FWD      NaN           NaN  
3797         9          4.638828      FWD      NaN           NaN  
2197         9          4.543693      MID      NaN           NaN  
1207         9          4.536190      MID      NaN           NaN  
3807         9          4.524833      MID      NaN           NaN


Gameweek 10:


name             team     opp_team  was_home  gameweek  \
2648      Mohamed Salah        Liverpool      Arsenal         0        10   
1308    Raheem Sterling          Chelsea       Wolves         1        10   
2818    Kevin De Bruyne  Manchester City  Southampton         1        10   
4408     Erling Haaland  Manchester City  Southampton         1        10   
2838       Riyad Mahrez  Manchester City  Southampton         1        10   
2988  Cristiano Ronaldo   Manchester Utd      Everton         0        10   
1208        Mason Mount          Chelsea       Wolves         1        10   
2918         Phil Foden  Manchester City  Southampton         1        10   
1178       Ben Chilwell          Chelsea       Wolves         1        10   
2858       Joao Cancelo  Manchester City  Southampton         1        10   
1098      Marcos Alonso          Chelsea       Wolves         1        10   
2118        Jamie Vardy   Leicester City  Bournemouth         0        10   
1248        Reece James          Chelsea       Wolves         1        10   
3798         Harry Kane        Tottenham     Brighton         0        10   
2848      Jack Grealish  Manchester City  Southampton         1        10   

      projected_points position  xPoints  total_points  
2648          6.366437      MID      NaN           NaN  
1308          6.287013      MID      NaN           NaN  
2818          5.931094      MID      NaN           NaN  
4408          5.783299      FWD      NaN           NaN  
2838          5.639885      MID      NaN           NaN  
2988          5.388312      FWD      NaN           NaN  
1208          5.367574      MID      NaN           NaN  
2918          5.122689      MID      NaN           NaN  
1178          4.990699      DEF      NaN           NaN  
2858          4.908767      DEF      NaN           NaN  
1098          4.883789      DEF      NaN           NaN  
2118          4.865793      FWD      NaN           NaN  
1248          4.838884      DEF      NaN           NaN  
3798          4.753438      FWD      NaN           NaN  
2848          4.717342      MID      NaN           NaN


Gameweek 11:


name             team         opp_team  was_home  gameweek  \
3799         Harry Kane        Tottenham          Everton         1        11   
3809      Heung-Min Son        Tottenham          Everton         1        11   
2649      Mohamed Salah        Liverpool  Manchester City         1        11   
1309    Raheem Sterling          Chelsea      Aston Villa         0        11   
2989  Cristiano Ronaldo   Manchester Utd    Newcastle Utd         1        11   
3969   Dejan Kulusevski        Tottenham          Everton         1        11   
4419       Ivan Perisic        Tottenham          Everton         1        11   
1209        Mason Mount          Chelsea      Aston Villa         0        11   
3039    Bruno Fernandes   Manchester Utd    Newcastle Utd         1        11   
4429       Darwin Nunez        Liverpool  Manchester City         1        11   
1409      Wilfried Zaha   Crystal Palace   Leicester City         0        11   
199       Gabriel Jesus          Arsenal     Leeds United         0        11   
99          Bukayo Saka          Arsenal     Leeds United         0        11   
1099      Marcos Alonso          Chelsea      Aston Villa         0        11   
2839       Riyad Mahrez  Manchester City        Liverpool         0        11   

      projected_points position  xPoints  total_points  
3799          6.802753      FWD      NaN           NaN  
3809          6.699168      MID      NaN           NaN  
2649          6.554761      MID      NaN           NaN  
1309          5.654763      MID      NaN           NaN  
2989          5.136993      FWD      NaN           NaN  
3969          4.867385      MID      NaN           NaN  
4419          4.854301      DEF      NaN           NaN  
1209          4.747318      MID      NaN           NaN  
3039          4.723998      MID      NaN           NaN  
4429          4.614263      FWD      NaN           NaN  
1409          4.536321      MID      NaN           NaN  
199           4.511514      FWD      NaN           NaN  
99            4.475416      MID      NaN           NaN  
1099          4.429405      DEF      NaN           NaN  
2839          4.373755      MID      NaN           NaN

In [13]:
# calculate cumulative xP for each player
projections.groupby(by=['name']).sum().sort_values(by='projected_points', ascending=False)['projected_points'].head(30)

name
Mohamed Salah             81.455400
Raheem Sterling           63.257865
Kevin De Bruyne           61.808019
Harry Kane                60.740531
Riyad Mahrez              55.621408
Erling Haaland            53.056540
Mason Mount               51.726854
Luis Diaz                 51.620951
Joao Cancelo              51.448607
Darwin Nunez              50.671234
Phil Foden                50.496854
Trent Alexander-Arnold    50.017497
Ben Chilwell              49.946905
Jack Grealish             49.539278
Cristiano Ronaldo         49.085649
Heung-Min Son             48.638222
Bukayo Saka               48.468849
Bruno Fernandes           47.990313
Andrew Robertson          47.779971
Reece James               47.723183
Ivan Toney                47.653011
Dejan Kulusevski          47.548756
Jamie Vardy               46.972214
Ivan Perisic              46.137990
Wilfried Zaha             45.311580
Ilkay Gundogan            44.773663
Jarrod Bowen              44.552487
Patrick Bamford        

In [48]:
projections[projections['name']=='Jack Grealish'].sort_values(by='gameweek')

name             team           opp_team  was_home  gameweek  \
41987  Jack Grealish  Manchester City           West Ham         0         1   
2840   Jack Grealish  Manchester City        Bournemouth         1         2   
2841   Jack Grealish  Manchester City      Newcastle Utd         0         3   
2842   Jack Grealish  Manchester City     Crystal Palace         1         4   
2843   Jack Grealish  Manchester City  Nottingham Forest         1         5   
2844   Jack Grealish  Manchester City        Aston Villa         0         6   
2845   Jack Grealish  Manchester City          Tottenham         1         7   
2846   Jack Grealish  Manchester City             Wolves         0         8   
2847   Jack Grealish  Manchester City     Manchester Utd         1         9   
2848   Jack Grealish  Manchester City        Southampton         1        10   
2849   Jack Grealish  Manchester City          Liverpool         0        11   

       projected_points position   xPoints  total_points  
41987          4.379329      NaN  4.116716           3.0  
2840           4.569909      MID       NaN           NaN  
2841           4.485911      MID       NaN           NaN  
2842           5.391105      MID       NaN           NaN  
2843           4.701261      MID       NaN           NaN  
2844           4.979311      MID       NaN           NaN  
2845           3.588996      MID       NaN           NaN  
2846           4.863992      MID       NaN           NaN  
2847           4.262062      MID       NaN           NaN  
2848           4.717342      MID       NaN           NaN  
2849           3.600059      MID       NaN           NaN

In [47]:
player_data[player_data['name']=='Raheem Sterling']

penalties_missed  influence   season  saves  transfers_in  \
41898                 0        7.0  2022-23      0         17941   

                  name  threat  was_home  transfers_out  minutes  \
41898  Raheem Sterling    56.0         0          61178       90   

       clean_sheets  goals_scored  own_goals  value  bps  assists  gameweek  \
41898             1             0          0   10.0   -1        0         1   

       penalties_saved  yellow_cards  ict_index               kickoff_time  \
41898                0             0        9.3  2022-08-06 16:30:00+00:00   

      opp_team  red_cards  goals_conceded position  creativity  \
41898  Everton          0               0      MID        29.8   

       transfers_balance  bonus    selected  total_points  General_#  \
41898             -43237      0  527937.249             3       17.0   

      General_Nation General_Pos General_Age  General_Min  Performance_Gls  \
41898        eng ENG       FW,LW      27-241         90.0                0   

       Performance_Ast  Performance_PK  Performance_PKatt  Performance_Sh  \
41898                0               0                  0               3   

       Performance_SoT  Performance_CrdY  Performance_CrdR  \
41898                0                 0                 0   

       Performance_Touches  Performance_Press  Performance_Tkl  \
41898                 46.0               13.0              1.0   

       Performance_Int  Performance_Blocks  Expected_xG  Expected_npxG  \
41898                0                 1.0          0.4            0.4   

       Expected_xA  SCA_SCA  SCA_GCA  Passes_Cmp  Passes_Att  Passes_Cmp%  \
41898          0.1      4.0      0.0        19.0        27.0         70.4   

       Passes_Prog  Carries_Carries  Carries_Prog  Dribbles_Succ  \
41898          4.0             43.0           7.0            4.0   

       Dribbles_Att     team  Total_Cmp  Total_Att  Total_Cmp%  Total_TotDist  \
41898           5.0  Chelsea       19.0       27.0        70.4          267.0   

       Total_PrgDist  Short_Cmp  Short_Att  Short_Cmp%  Medium_Cmp  \
41898           80.0       11.0       14.0        78.6         6.0   

       Medium_Att  Medium_Cmp%  Long_Cmp  Long_Att  Long_Cmp%  General_Ast  \
41898         8.0         75.0       0.0       1.0        0.0            0   

       General_xA  General_KP  General_1/3  General_PPA  General_CrsPA  \
41898         0.1         2.0          1.0          2.0            0.0   

       General_Prog  General_Att  Pass Types_Live  Pass Types_Dead  \
41898           4.0         27.0             27.0              0.0   

       Pass Types_FK  Pass Types_TB  Pass Types_Press  Pass Types_Sw  \
41898            0.0            0.0               8.0            1.0   

       Pass Types_Crs  Pass Types_CK  Corner Kicks_In  Corner Kicks_Out  \
41898               1            0.0              0.0               0.0   

       Corner Kicks_Str  Height_Ground  Height_Low  Height_High  \
41898               0.0           25.0         0.0          2.0   

       Body Parts_Left  Body Parts_Right  Body Parts_Head  Body Parts_TI  \
41898              5.0              22.0              0.0            0.0   

       Body Parts_Other  Outcomes_Cmp  Outcomes_Off  Outcomes_Out  \
41898               0.0          19.0           0.0           0.0   

       Outcomes_Int  Outcomes_Blocks  Tackles_Tkl  Tackles_TklW  \
41898           1.0              1.0          1.0             1   

       Tackles_Def 3rd  Tackles_Mid 3rd  Tackles_Att 3rd  Vs Dribbles_Tkl  \
41898              0.0              0.0              1.0              1.0   

       Vs Dribbles_Att  Vs Dribbles_Tkl%  Vs Dribbles_Past  Pressures_Press  \
41898              1.0             100.0               0.0             13.0   

       Pressures_Succ  Pressures_%  Pressures_Def 3rd  Pressures_Mid 3rd  \
41898             3.0         23.1                1.0                3.0   

       Pressures_Att 3rd  Blocks_Blocks  Blocks_Sh  

In [73]:
top_n = 10
min_minutes = 45

print('GOALKEEPERS')
print()
display(player_stats[(player_stats['minutes_played']>=min_minutes) & (player_stats['position']=='GK')]\
        .sort_values(by='value_points', ascending=False).head(top_n))

GOALKEEPERS



team position  price  minutes_played   xPoints  \
name                                                                           
Edouard Mendy              Chelsea       GK    5.0            90.0  6.346846   
David Raya               Brentford       GK    4.5            90.0  5.083261   
Jose Sa                     Wolves       GK    5.0            90.0  5.094675   
Ederson            Manchester City       GK    5.5            90.0  5.222209   
Danny Ward          Leicester City       GK    4.0            90.0  4.338147   
Nick Pope            Newcastle Utd       GK    5.0            90.0  4.720952   
Mark Travers           Bournemouth       GK    4.5            90.0  4.385586   
Emiliano Martinez      Aston Villa       GK    5.0            90.0  4.337465   
Hugo Lloris              Tottenham       GK    5.5            90.0  4.337465   
Illan Meslier         Leeds United       GK    4.5            90.0  3.763349   

                      value  value_points  
name                                       
Edouard Mendy      1.269369      2.838396  
David Raya         1.129614      2.396272  
Jose Sa            1.018935      2.278408  
Ederson            0.949493      2.226758  
Danny Ward         1.084537      2.169074  
Nick Pope          0.944190      2.111274  
Mark Travers       0.974575      2.067385  
Emiliano Martinez  0.867493      1.939773  
Hugo Lloris        0.788630      1.849501  
Illan Meslier      0.836300      1.774060

In [74]:
top_n = 20
min_minutes = 45

print('DEFENDERS')
print()
display(player_stats[(player_stats['minutes_played']>=min_minutes) & (player_stats['position']=='DEF')]\
        .sort_values(by='value_points', ascending=False).head(top_n))

DEFENDERS



team position  price  minutes_played  \
name                                                                   
Fabian Schar           Newcastle Utd      DEF    4.5            90.0   
Kieran Trippier        Newcastle Utd      DEF    5.0            90.0   
Dan Burn               Newcastle Utd      DEF    4.5            90.0   
Lloyd Kelly              Bournemouth      DEF    4.5            90.0   
Matt Targett           Newcastle Utd      DEF    5.0            90.0   
Oleksandr Zinchenko          Arsenal      DEF    5.1            82.0   
Cesar Azpilicueta            Chelsea      DEF    5.0            90.0   
Nathan Ake           Manchester City      DEF    5.0            90.0   
Timothy Castagne      Leicester City      DEF    4.5            90.0   
Eric Dier                  Tottenham      DEF    5.0            90.0   
Chris Mepham             Bournemouth      DEF    4.5            90.0   
Cristian Romero            Tottenham      DEF    5.0            90.0   
Diogo Dalot           Manchester Utd      DEF    4.5            90.0   
William Saliba               Arsenal      DEF    4.5            90.0   
Jordan Zemura            Bournemouth      DEF    4.5            90.0   
Kalidou Koulibaly            Chelsea      DEF    5.5            74.0   
Max Kilman                    Wolves      DEF    4.5            90.0   
Kyle Walker          Manchester City      DEF    5.0            90.0   
Thiago Silva                 Chelsea      DEF    5.5            90.0   
Ben Davies                 Liverpool      DEF    4.0            85.0   

                      xPoints     value  value_points  
name                                                   
Fabian Schar         7.814239  1.736498      3.683668  
Kieran Trippier      7.309747  1.461949      3.269018  
Dan Burn             6.636800  1.474844      3.128618  
Lloyd Kelly          6.539828  1.453295      3.082905  
Matt Targett         6.846488  1.369298      3.061843  
Oleksandr Zinchenko  6.676865  1.309189      2.956566  
Cesar Azpilicueta    6.075860  1.215172      2.717207  
Nathan Ake           5.822209  1.164442      2.603771  
Timothy Castagne     5.452990  1.211776      2.570564  
Eric Dier            5.732281  1.146456      2.563554  
Chris Mepham         5.303979  1.178662      2.500320  
Cristian Romero      5.538147  1.107629      2.476735  
Diogo Dalot          5.034077  1.118684      2.373087  
William Saliba       4.838702  1.075267      2.280986  
Jordan Zemura        4.813266  1.069615      2.268995  
Kalidou Koulibaly    5.264196  0.957127      2.244661  
Max Kilman           4.741911  1.053758      2.235358  
Kyle Walker          4.931969  0.986394      2.205644  
Thiago Silva         5.132281  0.933142      2.188412  
Ben Davies           4.347725  1.086931      2.173862

In [75]:
top_n = 20
min_minutes = 45

print('MIDFIELDERS')
print()
display(player_stats[(player_stats['minutes_played']>=min_minutes) & (player_stats['position']=='MID')]\
        .sort_values(by='value_points', ascending=False).head(top_n))

MIDFIELDERS



team position  price  minutes_played  \
name                                                                    
Pascal Gro                   Brighton      MID    5.5            90.0   
Dejan Kulusevski            Tottenham      MID    8.1            85.0   
Martinelli                    Arsenal      MID    6.1            90.0   
Joelinton               Newcastle Utd      MID    6.0            90.0   
Hwang Hee-chan                 Wolves      MID    6.0            84.0   
Daniel Podence                 Wolves      MID    5.5            90.0   
Jefferson Lerma           Bournemouth      MID    5.0            90.0   
Mohamed Salah               Liverpool      MID   13.0            90.0   
Kiernan Dewsbury-Hall  Leicester City      MID    5.0            72.0   
James Ward-Prowse         Southampton      MID    6.5            90.0   
Heung-Min Son               Tottenham      MID   12.0            90.0   
Joe Willock             Newcastle Utd      MID    5.0            79.0   
Eberechi Eze           Crystal Palace      MID    5.5            85.0   
Leander Dendoncker             Wolves      MID    5.0            90.0   
Allan Saint-Maximin     Newcastle Utd      MID    6.5            89.0   
N'Golo Kante                  Chelsea      MID    5.0            90.0   
Ruben Neves                    Wolves      MID    5.5            90.0   
Morgan Gibbs-White             Wolves      MID    5.5            90.0   
Bruno Guimaraes         Newcastle Utd      MID    6.0            89.0   
Bruno Fernandes        Manchester Utd      MID   10.0            89.0   

                         xPoints     value  value_points  
name                                                      
Pascal Gro             10.112627  1.838659      4.312039  
Dejan Kulusevski        7.468848  0.922080      2.624286  
Martinelli              5.923641  0.971089      2.398412  
Joelinton               5.781248  0.963541      2.360185  
Hwang Hee-chan          5.697652  0.949609      2.326057  
Daniel Podence          5.359739  0.974498      2.285401  
Jefferson Lerma         4.988753  0.997751      2.231038  
Mohamed Salah           7.988129  0.614471      2.215508  
Kiernan Dewsbury-Hall   4.648063  0.929613      2.078677  
James Ward-Prowse       4.949890  0.761522      1.941507  
Heung-Min Son           6.723602  0.560300      1.940937  
Joe Willock             4.270686  0.854137      1.909909  
Eberechi Eze            4.368403  0.794255      1.862693  
Leander Dendoncker      4.150035  0.830007      1.855952  
Allan Saint-Maximin     4.670686  0.718567      1.831994  
N'Golo Kante            3.737955  0.747591      1.671664  
Ruben Neves             3.888732  0.707042      1.658161  
Morgan Gibbs-White      3.849887  0.699979      1.641597  
Bruno Guimaraes         3.891650  0.648608      1.588759  
Bruno Fernandes         5.008691  0.500869      1.583887

In [76]:
top_n = 20
min_minutes = 45

print('FORWARDS')
print()
display(player_stats[(player_stats['minutes_played']>=min_minutes) & (player_stats['position']=='FWD')]\
        .sort_values(by='value_points', ascending=False).head(top_n))

FORWARDS



team position  price  minutes_played  \
name                                                                   
Aleksandar Mitrovic           Fulham      FWD    6.6            90.0   
Erling Haaland       Manchester City      FWD   11.6            77.0   
Danny Welbeck               Brighton      FWD    6.5            89.0   
Callum Wilson          Newcastle Utd      FWD    7.5            89.0   
Ivan Toney                 Brentford      FWD    7.0            90.0   
Kieffer Moore            Bournemouth      FWD    5.5            90.0   
Dominic Solanke          Bournemouth      FWD    6.0            89.0   
Bryan Mbeumo               Brentford      FWD    6.0            90.0   
Patrick Bamford         Leeds United      FWD    7.5            83.0   
Kai Havertz                  Chelsea      FWD    8.0            74.0   
Odsonne Edouard       Crystal Palace      FWD    5.5            57.0   
Harry Kane                 Tottenham      FWD   11.4            90.0   
Gabriel Jesus                Arsenal      FWD    8.0            82.0   
Danny Ings               Aston Villa      FWD    7.0            65.0   
Jamie Vardy           Leicester City      FWD    9.5            90.0   
Michail Antonio             West Ham      FWD    7.5            56.0   
Adam Armstrong           Southampton      FWD    5.5            45.0   
Roberto Firmino            Liverpool      FWD    8.0            50.0   

                       xPoints     value  value_points  
name                                                    
Aleksandar Mitrovic   8.468260  1.283070      3.296266  
Erling Haaland       11.123593  0.958930      3.265999  
Danny Welbeck         4.768566  0.733626      1.870385  
Callum Wilson         4.739920  0.631989      1.730774  
Ivan Toney            3.402481  0.486069      1.286017  
Kieffer Moore         2.796363  0.508430      1.192373  
Dominic Solanke       2.800089  0.466682      1.143132  
Bryan Mbeumo          2.704671  0.450779      1.104177  
Patrick Bamford       2.800749  0.373433      1.022689  
Kai Havertz           2.800063  0.350008      0.989972  
Odsonne Edouard       2.200008  0.400001      0.938086  
Harry Kane            3.000180  0.263174      0.888577  
Gabriel Jesus         2.400523  0.300065      0.848713  
Danny Ings            1.800044  0.257149      0.680353  
Jamie Vardy           2.031424  0.213834      0.659081  
Michail Antonio       1.800063  0.240008      0.657290  
Adam Armstrong        1.400044  0.254553      0.596981  
Roberto Firmino       1.000180  0.125023      0.353617

# My team

In [14]:
session = requests.session()

In [15]:
filepath = '../../../access_control/FPL_access.txt'
with open(filepath) as file:
    text = file.read().splitlines()
    email = text[0]
    password = text[1]

In [22]:
url = 'https://users.premierleague.com/accounts/login/'

payload = {
'password': password,
'login': email,
'redirect_uri': 'https://fantasy.premierleague.com/a/login', 
#"redirect_uri": "https://fantasy.premierleague.com/",
#'redirect_uri': 'https://fantasy.premierleague.com/api/bootstrap-static/',
'app': 'plfpl-web'
}

headers = {
   'authority': 'users.premierleague.com' ,
   'cache-control': 'max-age=0' ,
   'upgrade-insecure-requests': '1' ,
   'origin': 'https://fantasy.premierleague.com' ,
   'content-type': 'application/x-www-form-urlencoded' ,
   'user-agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_5) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/83.0.4103.116 Safari/537.36' ,
   'accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.9' ,
   'sec-fetch-site': 'same-site' ,
   'sec-fetch-mode': 'navigate' ,
   'sec-fetch-user': '?1' ,
   'sec-fetch-dest': 'document' ,
   'referer': 'https://fantasy.premierleague.com/my-team' ,
   'accept-language': 'en-US,en;q=0.9,he;q=0.8' ,
}

session.post(url, data=payload, headers=headers)

<Response [200]>

In [23]:
response = session.get('https://fantasy.premierleague.com/api/my-team/243790')
team = response.json()['picks']

In [24]:
my_player_ix = [player['element'] for player in team]
my_starting11 = my_player_ix[:-4]
my_subs = my_player_ix[-4:]

In [31]:
my_gameweek = gameweek+1
aux = projections[projections['gameweek']==my_gameweek]
expected_points = aux.loc[(aux['name'].isin(latest_fpl.loc[my_starting11, 'name'].values)), 'projected_points']
total_points = expected_points.sum() + expected_points.max()
print(f'Gameweek {my_gameweek}')
print(f'Projected points: {total_points}')
print()
print('Starting 11:')
display(aux.loc[(aux['name'].isin(latest_fpl.loc[my_starting11, 'name'].values))].sort_values(by='position'))
print()
print('Substitutes:')
display(aux.loc[(aux['name'].isin(latest_fpl.loc[my_subs, 'name'].values))].sort_values(by='projected_points',
                                                                                       ascending=False))

Gameweek 2
Projected points: 56.8221576

Starting 11:


name             team        opp_team  was_home  \
2630                 Alisson        Liverpool  Crystal Palace         1   
200      Oleksandr Zinchenko          Arsenal  Leicester City         1   
1240             Reece James          Chelsea       Tottenham         1   
2660  Trent Alexander-Arnold        Liverpool  Crystal Palace         1   
2790             Kyle Walker  Manchester City     Bournemouth         1   
2850            Joao Cancelo  Manchester City     Bournemouth         1   
150               Martinelli          Arsenal  Leicester City         1   
1200             Mason Mount          Chelsea       Tottenham         1   
2640           Mohamed Salah        Liverpool  Crystal Palace         1   
190            Gabriel Jesus          Arsenal  Leicester City         1   
4400          Erling Haaland  Manchester City     Bournemouth         1   

      gameweek  projected_points position  xPoints  total_points  
2630         2          3.860834       GK      NaN           NaN  
200          2          3.534308      DEF      NaN           NaN  
1240         2          3.391137      DEF      NaN           NaN  
2660         2          4.823452      DEF      NaN           NaN  
2790         2          4.166055      DEF      NaN           NaN  
2850         2          5.284076      DEF      NaN           NaN  
150          2          3.896891      MID      NaN           NaN  
1200         2          3.750883      MID      NaN           NaN  
2640         2          6.752071      MID      NaN           NaN  
190          2          4.913856      FWD      NaN           NaN  
4400         2          5.696524      FWD      NaN           NaN


Substitutes:


name            team        opp_team  was_home  gameweek  \
2000  Andreas Pereira          Fulham          Wolves         0         2   
2460    Sam Greenwood    Leeds United     Southampton         0         2   
2100       Danny Ward  Leicester City         Arsenal         0         2   
650      Josh Dasilva       Brentford  Manchester Utd         1         2   

      projected_points position  xPoints  total_points  
2000          2.531208      MID      NaN           NaN  
2460          2.376387      FWD      NaN           NaN  
2100          1.933203       GK      NaN           NaN  
650           1.893579      MID      NaN           NaN

# Data viz

In [62]:
fig = go.Figure()

players = ['Erling Haaland', 'Mohamed Salah']
colors = ['blue', 'red']

for count, player in enumerate(players):
    my_projections = projections[projections['name']==player].sort_values(by='gameweek')
    #my_projections['aux_var'] = my_projections['total_points'].copy()
    #my_projections.loc[my_projections['aux_var'].isnull(), 'aux_var'] = \
    #                            my_projections.loc[my_projections['aux_var'].isnull(), 'projected_points'].copy()
    
    fig.add_trace(
        go.Scatter(
            x=my_projections['gameweek'],
            #y=my_projections['total_points'],
            y=my_projections['xPoints'],
            mode="markers",
            marker=dict(color=colors[count]),
            #name=player + ' - actual',
            name=player + ' - xPoints',
            hovertext=('Opponent: ' + my_projections['opp_team'] + 
                       ', was_home: ' + my_projections['was_home'].astype(str)),
            showlegend=True,
            ),
    )
    
    fig.add_trace(
        go.Scatter(
            x=my_projections['gameweek'],
            y=my_projections['projected_points'],
            mode="markers+lines",
            marker=dict(color=colors[count]),
            name=player + ' - projected',
            hovertext=('Opponent: ' + my_projections['opp_team'] + 
                       ', was_home: ' + my_projections['was_home'].astype(str)),
            showlegend=True,
            ),
    )

fig.update_layout(
    #title="",
    template='plotly_dark',
    xaxis_title="gameweek",
    yaxis_title='projected_points',
    #showlegend=True
)